# 爬取KOL粉絲數、貼文和貼文按讚數


In [1]:
# Section 1: Imports
import time
from datetime import datetime
import re
from DrissionPage import errors
from DrissionPage import ChromiumPage
import mysql.connector
from mysql.connector import Error

## 2. 設定資料庫連接 

In [2]:
def create_connection():
    try:
        connection = mysql.connector.connect(
            host='127.0.0.1',
            database='kol_1017',
            user='root',
            password='123456789',
            port=3306
        )
        if connection.is_connected():
            return connection
    except Error as e:
        print(f"Error while connecting to MySQL: {e}")
    return None

def fetch_instagram_links(connection):
    """Fetch all Instagram links from the kol_radar_info table."""
    try:
        cursor = connection.cursor()
        query = "SELECT kol_ig_link FROM kol_radar_info WHERE kol_ig_link IS NOT NULL"
        cursor.execute(query)
        links = cursor.fetchall()
        return [link[0] for link in links]  # Extract links from tuples
    except Error as e:
        print(f"Error: {e}")
        return []
    finally:
        if cursor:
            cursor.close()


3. 抓取post數量和追蹤數

In [3]:
def fetch_post_links_with_ids(connection):
    """從 kol_post_data 表中提取所有 post_link 與對應的 account_id 並分類 post 和 reel。"""
    try:
        cursor = connection.cursor()
        query = "SELECT post_link, account_id FROM kol_post_data WHERE post_link IS NOT NULL"
        cursor.execute(query)
        links_with_ids = cursor.fetchall()
        # 返回一個包含 (post_link, account_id) 的列表
        return [{"post_link": link[0], "account_id": link[1]} for link in links_with_ids]
    except Error as e:
        print(f"Error: {e}")
        return []
    finally:
        if cursor:
            cursor.close()

def scrape_account_info(page, connection, ig_link):
    """Scrape basic account information from a given Instagram link using DrissionPage."""
    page.get(ig_link)
    time.sleep(5)  # Wait for page to load

    try:
        # Adjust the CSS selectors to match Instagram's structure
        account_nums = page.eles('.xl565be x1m39q7l x1uw6ca5 x2pgyrj', timeout=10)
        if len(account_nums) < 3:
            raise ValueError("Failed to locate necessary elements on the page.")

        post_num, followers_num, following_num = [num.text for num in account_nums[:3]]
        post_num = int(post_num.strip("貼文"))
        followers_num = followers_num.strip("位粉絲")
        if followers_num.endswith('萬'):
            followers_num = int(float(followers_num.strip('萬')) * 10000)
        else:
            followers_num = int(followers_num)
        following_num = int(following_num.strip("追蹤中"))

        account_id = page.ele(".x1lliihq x193iq5w x6ikm8r x10wlt62 xlyipyv xuxw1ft").text  # Extract account ID from the link
        insert_account_info(connection, account_id, post_num, followers_num, following_num)
        print(f'帳號: {account_id}, 貼文數: {post_num}, 粉絲數: {followers_num}, 追蹤數: {following_num}')
    except Exception as e:
        print(f"Error while scraping {ig_link}: {e}")




In [4]:
from DrissionPage import ChromiumPage
def main():
    connection = create_connection()
    if connection:
        links = fetch_instagram_links(connection)
        if not links:
            print("No Instagram links found.")
            return

        # Initialize DrissionPage
        page = ChromiumPage()
        for ig_link in links:
            try:
                scrape_account_info(page, connection, ig_link)
            except Exception as e:
                print(f"Error scraping {ig_link}: {e}")

        # Close DrissionPage and database connection
        page.quit()
        connection.close()

if __name__ == "__main__":
    main()

Error while scraping https://www.instagram.com/wu_11.16/: name 'insert_account_info' is not defined


KeyboardInterrupt: 

1/2
鎖定圖片

每位網紅能抓多少盡量抓

某個時間區間看可以抓多少數量，如果太少再拉長時間區間

可以分成post為主的跟reels為主的，其他特徵可以之後再加

圖片存起來

從 MySQL 資料庫讀取 kol_ig_id 作為 account。

區分影片和圖片，並統計發文類型。

根據文章時間決定爬取範圍，當文章時間早於 2023/01/01 時停止。

In [6]:
def insert_posts_likes_comments(connection, ig_post_id, account_id, likes_count, comments_count):
    try:
        cursor = connection.cursor()
        query = """INSERT INTO PostsLikesComments (ig_post_id, account_id, likes_count, comments_count) 
                   VALUES (%s, %s, %s, %s)
                   ON DUPLICATE KEY UPDATE 
                   likes_count = VALUES(likes_count),
                   comments_count = VALUES(comments_count)"""
        cursor.execute(query, (ig_post_id, account_id, likes_count, comments_count))
        connection.commit()
    except Error as e:
        print(f"Error: {e}")
    finally:
        if cursor:
            cursor.close()

def insert_posts_details(connection, post_id, account_id, post_text, hashtags, product_links, mentions, img_url, post_datetime, partner_id):
    try:
        cursor = connection.cursor()
        query = """INSERT INTO PostsDetails 
                   (post_id, account_id, post_text, hashtags, product_links, mentions, img_url, post_datetime, partner_id) 
                   VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s)
                   ON DUPLICATE KEY UPDATE 
                   post_text = VALUES(post_text),
                   hashtags = VALUES(hashtags),
                   product_links = VALUES(product_links),
                   mentions = VALUES(mentions),
                   img_url = VALUES(img_url),
                   post_datetime = VALUES(post_datetime),
                   partner_id = VALUES(partner_id)"""
        cursor.execute(query, (post_id, account_id, post_text, hashtags, product_links, mentions, img_url, post_datetime, partner_id))
        connection.commit()
    except Error as e:
        print(f"Error: {e}")
    finally:
        if cursor:
            cursor.close()

In [ ]:
# def scrape_post_details(page, connection, account, post_idx):
#     """Scrape detailed information for each post"""
#     first_post = page.ele('._aagw')
#     first_post.click()
#     pop_window_ele = page.ele('.x1cy8zhl x9f619 x78zum5 xl56j7k x2lwn1j xeuugli x47corl')
#     for j in range():
#         print(f'帳號: {account} === 第 {j + 1} 個 Post ===')
#         retry_count = 0
#         img_url = ''
#         post_text = ''
#         while retry_count < 2:
#             try:
#                 post_text_ele = pop_window_ele.ele('._ap3a _aaco _aacu _aacx _aad7 _aade')
#                 post_text = post_text_ele.text
#                 print('post_text:', post_text)

#                 hashtags = ', '.join(re.findall(r'#\w+', post_text))
#                 product_links = ', '.join(re.findall(r'https?://\S+', post_text))
#                 mentions = ', '.join(re.findall(r'@\w+', post_text))
                
#                 time_element = pop_window_ele.ele('.x1p4m5qa', timeout=5)
#                 img = pop_window_ele.ele('.x5yr21d xu96u03 x10l6tqk x13vifvy x87ps6o xh8yej3', timeout=2)
#                 img_url = img.attr('src')
#                 post_datetime = (time_element.attr('datetime')) if time_element else None

#                 if post_datetime:
#                     try:
#                         dt = datetime.strptime(post_datetime, "%Y-%m-%dT%H:%M:%S.%fZ")
#                         post_datetime = dt.strftime("%Y-%m-%d %H:%M:%S")
#                     except ValueError:
#                         print(f"無法解析日期時間: {post_datetime}")
#                         post_datetime = None

#                 partner_ele = page.ele('._aaql')
#                 partner_id = partner_ele.text if partner_ele and partner_ele.text.strip() != '' else None    
                
#                 post_id = f'{account}_{str(post_idx).zfill(4)}'
#                 insert_posts_details(connection, post_id, account, post_text, hashtags, product_links, mentions, img_url, post_datetime, partner_id)
                
#                 break
#             except errors.ElementNotFoundError:
#                 print('該 post 為影片')
#                 post_idx += 1
#                 break
#             except errors.ElementLostError:
#                 retry_count += 1
#                 print('retry:', retry_count)
#                 time.sleep(3)
        
#         post_idx += 1
#         next_btm = pop_window_ele.ele('. _aaqg _aaqh')
#         next_btm.click()

In [ ]:
# import mysql.connector
# from datetime import datetime
# import time
# import re

# def create_connection():
#     try:
#         connection = mysql.connector.connect(
#             host='127.0.0.1',
#             database='kol_1017',
#             user='root',
#             password='123456789',
#             port=3306
#         )
#         if connection.is_connected():
#             return connection
#     except Error as e:
#         print(f"Error while connecting to MySQL: {e}")
#     return None



# def get_post_num(connection, kol_ig_id):
#     """ 從資料庫取得該 KOL 的 post 總數 """
#     cursor = connection.cursor(dictionary=True)
#     query = f"SELECT post_num FROM kol_1017.accountinfo WHERE account_id = '{kol_ig_id}';"  # Use the correct column name
#     cursor.execute(query)
#     result = cursor.fetchone()
#     cursor.close()
#     return result["post_num"] if result else None

# # 測試
# connection = create_connection()
# kol_accounts = get_kol_accounts(connection)
# for kol_ig_id in kol_accounts[:3]:
#     post_num = get_post_num(connection, kol_ig_id)
#     if post_num is not None:
#         print(f"{kol_ig_id}: {post_num} 則貼文")
#     else:
#         print(f"{kol_ig_id}: No post_num found")
# connection.close()

wu_11.16: 125 則貼文
perrygreeeen: 204 則貼文
araiyuka: 260 則貼文


In [7]:
import mysql.connector
from mysql.connector import Error
from datetime import datetime
import time
import re
from DrissionPage import ChromiumPage

def get_kol_accounts(connection):
    """ 從資料庫取得所有 KOL Instagram ID """
    cursor = connection.cursor(dictionary=True)
    query = "SELECT kol_ig_id FROM kol_1017.kol_radar_info;"
    cursor.execute(query)
    kol_accounts = [row["kol_ig_id"] for row in cursor.fetchall()]
    cursor.close()
    return kol_accounts

def insert_posts_likes_comments(connection, post_id, account, likes, comments):
    """插入按讚數與留言數至資料庫"""
    try:
        cursor = connection.cursor()
        query = """
            INSERT INTO kol_1017.posts_likes_comments (post_id, account_id, likes_count, comments_count)
            VALUES (%s, %s, %s, %s)
            ON DUPLICATE KEY UPDATE likes_count=%s, comments_count=%s;
        """
        cursor.execute(query, (post_id, account, likes, comments, likes, comments))
        connection.commit()
        cursor.close()
    except Error as e:
        print(f"Error while inserting likes/comments: {e}")

def get_post_num(connection, kol_ig_id):
    """ 從資料庫取得該 KOL 帳號的貼文總數 """
    cursor = connection.cursor(dictionary=True)
    query = f"SELECT post_num FROM kol_1017.accountinfo WHERE account_id = '{kol_ig_id}';"
    cursor.execute(query)
    result = cursor.fetchone()
    cursor.close()
    return result["post_num"] if result else None

def insert_post_data(connection, account, post_key, likes_count, comments_count, full_link):
    """ 插入 Instagram 貼文資料至資料庫 """
    cursor = connection.cursor()
    insert_query = '''
    INSERT INTO kol_post_data (account_id, post_key, likes_count, comments_count, post_link)
    VALUES (%s, %s, %s, %s, %s);
    '''
    data = (account, post_key, likes_count, comments_count, full_link)
    cursor.execute(insert_query, data)
    connection.commit()
    cursor.close()

def delete_kol_data(connection, account):
    """ 刪除該 KOL 在資料庫中的資料 """
    cursor = connection.cursor()
    try:
        delete_query = "DELETE FROM kol_post_data WHERE account_id = %s;"
        cursor.execute(delete_query, (account,))
        connection.commit()
        print(f"已刪除帳號 {account} 的資料。")
    except Exception as e:
        print(f"刪除帳號 {account} 的資料時發生錯誤：{e}")
    finally:
        cursor.close()


In [1]:
from DrissionPage.errors import *
def scrape_instagram_posts(account, target_post_num, connection):
    """ 爬取 Instagram 貼文資訊並存入資料庫 """
    page = ChromiumPage()
    page.get(f'https://www.instagram.com/{account}/')
    page.wait(5)

    post_set = set()
    unique_posts = []
    post_number = 1
    post_dict = {}
    no_new_post_count = 0  # 記錄連續無新貼文次數
    consecutive_fail_count = 0  # 連續失敗次數
    total_fail_count = 0  # 累積失敗次數
    skip_kol=[]
    #抓取貼文連結
    for i in range(20):
        page.scroll.down(80) # 向下滾動
        page.wait(2)  # 等待頁面加載
        posts = page.eles('.x1lliihq x1n2onr6 xh8yej3 x4gyw5p x1ntc13c x9i3mqj x11i5rnm x2pgyrj')  # 重新讀取貼文列表
        added_new_post = False  # 判斷這次爬取是否有新增貼文
        
        for post in posts:
            a_tag = post.ele('.x1i10hfl xjbqb8w x1ejq31n xd10rxx x1sy0etr x17r0tee x972fbf xcfux6l x1qhh985 xm0m39n x9f619 x1ypdohk xt0psk2 xe8uvvx xdj266r x11i5rnm xat24cr x1mh8g0r xexx8yu x4uap5 x18d9i69 xkhd6sd x16tdsg8 x1hl2dhg xggy1nq x1a2a7pz _a6hd')  # 從 post 抓取 <a> 標籤
            if a_tag:
                link = a_tag.attr('href')
                # 篩選符合 "/reel/" 或 "/p/" 的連結
                if f"{account}/reel/" in link or f"{account}/p/" in link:
                    if link not in post_set:
                        # 數據
                        try:
                            try:
                                post.scroll.to_half()
                                post.hover()
                            except NoRectError:
                                print("無法定位該元素，跳過該貼文。")
                                page.scroll.to_bottom()
                                continue  # 跳過該貼文
                            # 如果找不到元素，就跳過這個貼文
                            

                            common_class = 'x972fbf xcfux6l x1qhh985 xm0m39n x3nfvp2 x15zctf7 xln7xf2 xk390pu xdj266r x1mh8g0r x1j4z8aw x2pgyrj xl1lypt x5th0yj xexx8yu x4uap5 x18d9i69 xkhd6sd x11njtxf'
                            elements = post.eles(f'.{common_class}', timeout=2)

                             # 檢查按讚數是否存在
                            if len(elements) < 2:
                                print("按讚數或留言數被隱藏，跳過此貼文。")
                                consecutive_fail_count += 1  # 連續失敗次數加 1
                                total_fail_count += 1  # 累積失敗次數加 1
                                if consecutive_fail_count >= 10 or total_fail_count >= 40:
                                    print(f"{account} 累積 {total_fail_count} 次或連續 {consecutive_fail_count} 次獲取失敗，跳過該 KOL。")
                                    skip_kol.append(account)
                                    delete_kol_data(connection, account)  # 刪除 KOL 資料
                                    return
                                continue
                            
                            #如果大於等於2
                            elif len(elements) == 2 or len(elements) > 2:
                                # 如果成功獲取數據，重置連續失敗次數
                                consecutive_fail_count = 0
                                full_link = link  # 加上完整網址
                                post_key = f"{account}_{post_number:03d}"  # 編號鍵值
                                post_dict[post_key] = full_link  # 加入字典
                                post_number += 1  # 編號遞增
                                added_new_post = True  # 新增貼文
                                post_set.add(link)
                                unique_posts.append(full_link)
                                likes_count = elements[0].text
                                if likes_count.endswith('萬'):
                                    likes_count = int(float(likes_count.strip('萬')) * 10000)
                                else:
                                    likes_count = int(likes_count)

                                comments_count = elements[1].text
                                if comments_count.endswith('萬'):
                                    comments_count = int(float(comments_count.strip('萬')) * 10000)
                                else:
                                    comments_count = int(comments_count)

                                print(f"帳號: {account}, 編號: {post_key}, 按讚數: {likes_count}, 留言數: {comments_count}, 連結: {full_link}")
                                insert_post_data(connection, post_key, account, likes_count, comments_count, full_link)
                                
                                # 當達到 target_post_num 時，結束爬取，換下一個 KOL
                                if post_number > target_post_num:
                                    return
                        except IndexError:
                            print("發生 IndexError，跳過此貼文。")
                            continue  # 當 `elements` 長度不足時跳過

            else:
                print("未找到 <a> 標籤")
        # 檢查這次爬取是否有新增貼文
        if not added_new_post:
            no_new_post_count += 1  # 無新增貼文次數加 1
            print(f"第 {i + 1} 次爬取無新增貼文，連續無新貼文次數：{no_new_post_count}")
            if no_new_post_count >= 3:  # 若連續 3 次無新貼文，結束爬取
                print(f"{account} 貼文數量不足，換下一個 KOL")
                break
        else:
            no_new_post_count = 0  # 如果有新增貼文，重置計數
            # page.wait(2)

        print(f"不重複的貼文數量：{len(unique_posts)}")
        # 顯示有哪些 KOL 被跳過
    print("跳過的 KOL：", skip_kol)
#    
def main():
    connection = create_connection()
    if not connection:
        print("無法建立資料庫連線")
        return
    kol_accounts = get_kol_accounts(connection)
    print(f"找到 {len(kol_accounts)} 個 KOL 帳號")

    #只要最後一個帳號
    for account in kol_accounts[-1:]:
        print(f"開始抓取帳號：{account}")
        post_num = get_post_num(connection, account)
        print(f"帳號: {account}, 貼文數: {post_num}")
        if post_num is None:
            print(f"帳號 {account} 無 post_num 資料，跳過。")
            continue

        target_post_num = min(post_num, 100)
        print(f"開始抓取帳號：{account}，預計抓取貼文數量：{target_post_num}")
        scrape_instagram_posts(account, target_post_num, connection)
        print(f"帳號 {account} 貼文抓取完成，還剩下{len(kol_accounts) - kol_accounts.index(account) - 1}個帳號。")
        print("-" * 50)
    
    connection.close()


In [2]:
from DrissionPage import ChromiumPage

url = 'https://www.instagram.com/isx_o6'
page = ChromiumPage()
page.get(url)

True

In [16]:
if __name__ == '__main__':
    main()

找到 555 個 KOL 帳號
開始抓取帳號：molly_chiang
帳號: molly_chiang, 貼文數: 891000
開始抓取帳號：molly_chiang，預計抓取貼文數量：100
帳號: molly_chiang, 編號: molly_chiang_001, 按讚數: 12000, 留言數: 161, 連結: https://www.instagram.com/molly_chiang/p/Cttow5sS8O4/
帳號: molly_chiang, 編號: molly_chiang_002, 按讚數: 609000, 留言數: 948, 連結: https://www.instagram.com/molly_chiang/reel/CPQarRsBAMb/
帳號: molly_chiang, 編號: molly_chiang_003, 按讚數: 27000, 留言數: 305, 連結: https://www.instagram.com/molly_chiang/p/B3D781tnmWo/
帳號: molly_chiang, 編號: molly_chiang_004, 按讚數: 5675, 留言數: 172, 連結: https://www.instagram.com/molly_chiang/reel/DEzvjSUyIGS/
帳號: molly_chiang, 編號: molly_chiang_005, 按讚數: 12000, 留言數: 357, 連結: https://www.instagram.com/molly_chiang/p/DEpkJQ8SUz4/
帳號: molly_chiang, 編號: molly_chiang_006, 按讚數: 2992, 留言數: 238, 連結: https://www.instagram.com/molly_chiang/reel/DEkSucBycEc/
帳號: molly_chiang, 編號: molly_chiang_007, 按讚數: 6507, 留言數: 225, 連結: https://www.instagram.com/molly_chiang/reel/DEht_tFS7AK/
帳號: molly_chiang, 編號: molly_chiang_008, 按讚數: 6656, 

In [145]:

if __name__ == '__main__':
    main()

找到 554 個 KOL 帳號
帳號: wu_11.16, 貼文數: 125
開始抓取帳號：wu_11.16，預計抓取貼文數量：100
帳號: wu_11.16, 編號: wu_11.16_001, 按讚數: 926, 留言數: 16, 連結: https://www.instagram.com/wu_11.16/reel/DEhPOJRyRE_/
帳號: wu_11.16, 編號: wu_11.16_002, 按讚數: 10000, 留言數: 69, 連結: https://www.instagram.com/wu_11.16/reel/DDRWu7cPYzl/
帳號: wu_11.16, 編號: wu_11.16_003, 按讚數: 6656, 留言數: 247, 連結: https://www.instagram.com/wu_11.16/reel/DDCEC89yVsp/
帳號: wu_11.16, 編號: wu_11.16_004, 按讚數: 65000, 留言數: 1366, 連結: https://www.instagram.com/wu_11.16/reel/DCTdPV5yL_M/
帳號: wu_11.16, 編號: wu_11.16_005, 按讚數: 914, 留言數: 18, 連結: https://www.instagram.com/wu_11.16/reel/DBvhTE1Swez/
帳號: wu_11.16, 編號: wu_11.16_006, 按讚數: 2473, 留言數: 58, 連結: https://www.instagram.com/wu_11.16/reel/DBdafrNSkyr/
帳號: wu_11.16, 編號: wu_11.16_007, 按讚數: 24000, 留言數: 1832, 連結: https://www.instagram.com/wu_11.16/reel/DA-kOIJyY-9/
帳號: wu_11.16, 編號: wu_11.16_008, 按讚數: 543, 留言數: 14, 連結: https://www.instagram.com/wu_11.16/reel/C_Fmc0syMHw/
帳號: wu_11.16, 編號: wu_11.16_009, 按讚數: 57, 留言數: 0, 連結: ht

ElementLostError: 元素对象已失效。可能是页面整体刷新，或js局部刷新把元素替换或去除了。

In [154]:
if __name__ == "__main__":
    main()

找到 554 個 KOL 帳號
帳號: eatzzz7, 貼文數: 5345
開始抓取帳號：eatzzz7，預計抓取貼文數量：100
帳號: eatzzz7, 編號: eatzzz7_001, 按讚數: 4007, 留言數: 29, 連結: https://www.instagram.com/eatzzz7/p/DEeE65QTRtO/
帳號: eatzzz7, 編號: eatzzz7_002, 按讚數: 5598, 留言數: 41, 連結: https://www.instagram.com/eatzzz7/reel/DEW6XXaPILI/
帳號: eatzzz7, 編號: eatzzz7_003, 按讚數: 12000, 留言數: 31, 連結: https://www.instagram.com/eatzzz7/p/DEVO4KzSoqR/
帳號: eatzzz7, 編號: eatzzz7_004, 按讚數: 10000, 留言數: 61, 連結: https://www.instagram.com/eatzzz7/reel/DEPYozyv0sh/
帳號: eatzzz7, 編號: eatzzz7_005, 按讚數: 16000, 留言數: 60, 連結: https://www.instagram.com/eatzzz7/p/DEKRxGuPG_R/
帳號: eatzzz7, 編號: eatzzz7_006, 按讚數: 12000, 留言數: 74, 連結: https://www.instagram.com/eatzzz7/reel/DEH8xjovbfu/
帳號: eatzzz7, 編號: eatzzz7_007, 按讚數: 17000, 留言數: 85, 連結: https://www.instagram.com/eatzzz7/p/DD_RFjOvtsk/
帳號: eatzzz7, 編號: eatzzz7_008, 按讚數: 5840, 留言數: 32, 連結: https://www.instagram.com/eatzzz7/p/DD7BLI4Ppxw/
帳號: eatzzz7, 編號: eatzzz7_009, 按讚數: 12000, 留言數: 36, 連結: https://www.instagram.com/eatzzz7/p/DD1h

## 抓取貼文連結與按讚數、留言數

In [ ]:
from DrissionPage import ChromiumPage

account = "perrygreeeen"
page.get(f'https://www.instagram.com/{account}/')
page.wait(5)

post_set = set()
unique_posts = []
post_number = 1
post_dict = {}

# 抓取貼文連結
for i in range(5):
    page.scroll.to_bottom()  # 向下滾動
    posts = page.eles('.x1lliihq.x1n2onr6.xh8yej3.x4gyw5p.x1ntc13c.x9i3mqj.x11i5rnm.x2pgyrj')  # 重新讀取貼文列表
    for post in posts:
        try:
            a_tag = post.ele('.x1i10hfl.xjbqb8w.x1ejq31n.xd10rxx.x1sy0etr.x17r0tee.x972fbf.xcfux6l.x1qhh985.xm0m39n.x9f619.x1ypdohk.xt0psk2.xe8uvvx.xdj266r.x11i5rnm.xat24cr.x1mh8g0r.xexx8yu.x4uap5.x18d9i69.xkhd6sd.x16tdsg8.x1hl2dhg.xggy1nq.x1a2a7pz._a6hd')  # 從 post 抓取 <a> 標籤
            if a_tag:
                link = a_tag.attr('href')
                print('link:', link)    
                if f"{account}/reel/" in link or f"{account}/p/" in link:
                    if link not in post_set:
                        full_link = f"https://www.instagram.com{link}"  # 加上完整網址
                        post_key = f"{account}_{post_number:03d}"  # 編號鍵值
                        post_dict[post_key] = full_link  # 加入字典
                        post_number += 1  # 編號遞增

                        post_set.add(full_link)
                        unique_posts.append(full_link)
                        
                        page.wait(1)  # 等待貼文完整顯示
                        post.hover()  # 滑鼠移至貼文
                        common_class = '.x972fbf xcfux6l x1qhh985 xm0m39n x3nfvp2 x15zctf7 xln7xf2 xk390pu xdj266r x1mh8g0r x1j4z8aw x2pgyrj xl1lypt x5th0yj xexx8yu x4uap5 x18d9i69 xkhd6sd x11njtxf'
                        elements = post.eles(f'.{common_class}', timeout=10)
                        likes_count = elements[0].text if len(elements) > 0 else "無法獲取按讚數"
                        comments_count = elements[1].text if len(elements) > 1 else "無法獲取留言數"
                        
                        print(f"帳號: {account}, 編號: {post_key}, 按讚數: {likes_count}, 留言數: {comments_count}, 連結: {full_link}")
        except Exception as e:
            print(f"發生錯誤：{e}")

print(f"不重複的貼文數量：{len(unique_posts)}")


KeyboardInterrupt: 

In [75]:
from DrissionPage import ChromiumPage

account = "perrygreeeen"
page.get(f'https://www.instagram.com/{account}/')
page.wait(5)

post_set = set()
unique_posts = []
post_number = 1
post_dict = {} 

#抓取貼文連結
for i in range(20):
    page.scroll.down(80) # 向下滾動
    page.wait(2)  # 等待頁面加載
    posts = page.eles('.x1lliihq x1n2onr6 xh8yej3 x4gyw5p x1ntc13c x9i3mqj x11i5rnm x2pgyrj')  # 重新讀取貼文列表
    for post in posts:
        a_tag = post.ele('.x1i10hfl xjbqb8w x1ejq31n xd10rxx x1sy0etr x17r0tee x972fbf xcfux6l x1qhh985 xm0m39n x9f619 x1ypdohk xt0psk2 xe8uvvx xdj266r x11i5rnm xat24cr x1mh8g0r xexx8yu x4uap5 x18d9i69 xkhd6sd x16tdsg8 x1hl2dhg xggy1nq x1a2a7pz _a6hd')  # 從 post 抓取 <a> 標籤
        if a_tag:
            link = a_tag.attr('href')
            # 篩選符合 "/reel/" 或 "/p/" 的連結
            if f"{account}/reel/" in link or f"{account}/p/" in link:
                if link not in post_set:
                    full_link = f"https://www.instagram.com{link}"  # 加上完整網址
                    post_key = f"{account}_{post_number:03d}"  # 編號鍵值
                    post_dict[post_key] = full_link  # 加入字典
                    post_number += 1  # 編號遞增
                    post_set.add(link)
                    unique_posts.append(full_link)
                    #數據
                    post.hover()
                    common_class = 'x972fbf xcfux6l x1qhh985 xm0m39n x3nfvp2 x15zctf7 xln7xf2 xk390pu xdj266r x1mh8g0r x1j4z8aw x2pgyrj xl1lypt x5th0yj xexx8yu x4uap5 x18d9i69 xkhd6sd x11njtxf'
                    elements = page.eles(f'.{common_class}', timeout=10)
                    likes_count = elements[0].text
                    if likes_count.endswith('萬'):
                        likes_count = int(float(likes_count.strip('萬')) * 10000)
                    else:
                        likes_count = int(likes_count)
                    comments_count = elements[1].text
                    if comments_count.endswith('萬'):
                        comments_count = int(float(comments_count.strip('萬')) * 10000)
                    else:
                        comments_count = int(comments_count)
                    print(f"帳號: {account}, 編號: {post_key}, 按讚數: {likes_count}, 留言數: {comments_count}, 連結: {full_link}")
        else:
            print("未找到 <a> 標籤")

        # page.wait(2)

print(f"不重複的貼文數量：{len(unique_posts)}")


print(post_dict)

帳號: perrygreeeen, 編號: perrygreeeen_001, 按讚數: 284000, 留言數: 1938, 連結: https://www.instagram.comhttps://www.instagram.com/perrygreeeen/reel/DAN06m8sQyJ/
帳號: perrygreeeen, 編號: perrygreeeen_002, 按讚數: 131000, 留言數: 1149, 連結: https://www.instagram.comhttps://www.instagram.com/perrygreeeen/reel/C_A3N3VvgSn/
帳號: perrygreeeen, 編號: perrygreeeen_003, 按讚數: 13000, 留言數: 85, 連結: https://www.instagram.comhttps://www.instagram.com/perrygreeeen/reel/C8ertUfPzgb/
帳號: perrygreeeen, 編號: perrygreeeen_004, 按讚數: 33, 留言數: 0, 連結: https://www.instagram.comhttps://www.instagram.com/perrygreeeen/reel/DEhkHuXTqbZ/
帳號: perrygreeeen, 編號: perrygreeeen_005, 按讚數: 660, 留言數: 3, 連結: https://www.instagram.comhttps://www.instagram.com/perrygreeeen/p/DEfJyhqzDq5/
帳號: perrygreeeen, 編號: perrygreeeen_006, 按讚數: 3189, 留言數: 44, 連結: https://www.instagram.comhttps://www.instagram.com/perrygreeeen/reel/DEUyh1ITHe_/
帳號: perrygreeeen, 編號: perrygreeeen_007, 按讚數: 791, 留言數: 19, 連結: https://www.instagram.comhttps://www.instagram.com/perrygree

KeyboardInterrupt: 